In [ ]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import zipfile
import os
from pickle import dump,load
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression as LR
from sklearn.metrics import plot_confusion_matrix
from sklearn.model_selection import GridSearchCV

pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)

In [105]:
#loading data set from fivethirtyeight.com
zf = zipfile.ZipFile('soccer-spi.zip')
raw_data=pd.read_csv(zf.open("soccer-spi/spi_matches_latest.csv"))
try:
    os.mkdir("data_sets")
except:
    "File Already Exists"
    pass


In [3]:
raw_data.head()

season        date  league_id                league                 team1  \
0    2019  2019-03-01       1979  Chinese Super League       Shandong Luneng   
1    2019  2019-03-01       1979  Chinese Super League  Guangzhou Evergrande   
2    2019  2019-03-01       1979  Chinese Super League    Shanghai Greenland   
3    2019  2019-03-01       1979  Chinese Super League            Wuhan Zall   
4    2019  2019-03-01       1979  Chinese Super League       Chongqing Lifan   

               team2   spi1   spi2   prob1   prob2  probtie  proj_score1  \
0      Guizhou Renhe  48.22  37.83  0.5755  0.1740   0.2505         1.75   
1  Tianjin Quanujian  65.59  39.99  0.7832  0.0673   0.1495         2.58   
2      Shanghai SIPG  39.81  60.08  0.2387  0.5203   0.2410         1.22   
3      Beijing Guoan  32.25  54.82  0.2276  0.5226   0.2498         1.10   
4       Guangzhou RF  38.24  40.45  0.4403  0.2932   0.2665         1.57   

   proj_score2  importance1  importance2  score1  score2   xg1   xg2  nsxg1  \
0         0.84         45.9         22.1     1.0     0.0  1.39  0.26   2.05   
1         0.62         77.1         28.8     3.0     0.0  0.49  0.45   1.05   
2         1.89         25.6         63.4     0.0     4.0  0.57  2.76   0.80   
3         1.79         35.8         58.9     0.0     1.0  1.12  0.97   1.51   
4         1.24         26.2         21.3     2.0     2.0  2.77  3.17   1.05   

   nsxg2  adj_score1  adj_score2  
0   0.54        1.05        0.00  
1   0.75        3.15        0.00  
2   1.50        0.00        3.26  
3   0.94        0.00        1.05  
4   2.08        2.10        2.10

In [5]:
leagues = ['Belgian Jupiler League', 'French Ligue 1', 'Turkish Turkcell Super Lig', 'Barclays Premier League', 'Spanish Primera Division', 'Dutch Eredivisie', 'Portuguese Liga', 'German Bundesliga', 'Italy Serie A']

In [7]:
#Collecting indexs of relevant leagues
indexes = []
for league in leagues:
    indexes.extend(raw_data["league"][lambda x: x == league ].index)
    
#creating the data set
leagues_datas = raw_data.loc[indexes].rename(columns = { "team1" : "HomeTeam" ,"team2" : "AwayTeam" }).reset_index(drop = True)
leagues_datas["date"]= leagues_datas.apply(lambda row: "/".join(row["date"].split("-")[::-1])[0:6] + "/".join(row["date"].split("-")[::-1])[-2:], axis=1)
leagues_datas["league"] = leagues_datas["league"].map({'Belgian Jupiler League' : 'belgium', 'French Ligue 1' : 'france', 'Turkish Turkcell Super Lig' : 'turkey', 
                                                       'Barclays Premier League' : 'england', 'Spanish Primera Division' : 'spain', 
                                                       'Dutch Eredivisie' : 'netherland', 'Portuguese Liga' : 'portugal', 
                                                       'German Bundesliga' : 'germany', 'Italy Serie A' : 'italy'}) 

In [8]:
#Leagues Datas With Relevant Features
leagues_datas = leagues_datas.iloc[:,:17]
leagues_datas

season      date  league_id      league                  HomeTeam  \
0       2020  08/08/20       1832     belgium               Club Brugge   
1       2020  08/08/20       1832     belgium            Standard Liege   
2       2020  08/08/20       1832     belgium                   Antwerp   
3       2020  09/08/20       1832     belgium             St. Truidense   
4       2020  09/08/20       1832     belgium          SV Zulte Waregem   
5       2020  09/08/20       1832     belgium               KV Mechelen   
6       2020  09/08/20       1832     belgium               KV Kortrijk   
7       2020  10/08/20       1832     belgium                 OH Leuven   
8       2020  10/08/20       1832     belgium               KV Oostende   
9       2020  14/08/20       1832     belgium         Mouscron-Peruwelz   
10      2020  15/08/20       1832     belgium                      Genk   
11      2020  15/08/20       1832     belgium                  KAA Gent   
12      2020  15/08/20       1832     belgium     Sporting de Charleroi   
13      2020  16/08/20       1832     belgium             Cercle Brugge   
14      2020  16/08/20       1832     belgium    KFCO Beerschot-Wilrijk   
15      2020  16/08/20       1832     belgium                     Eupen   
16      2020  16/08/20       1832     belgium                Anderlecht   
17      2020  17/08/20       1832     belgium          Waasland-Beveren   
18      2020  21/08/20       1832     belgium               KV Kortrijk   
19      2020  22/08/20       1832     belgium          SV Zulte Waregem   
20      2020  22/08/20       1832     belgium               KV Mechelen   
21      2020  22/08/20       1832     belgium                 OH Leuven   
22      2020  22/08/20       1832     belgium                   Antwerp   
23      2020  23/08/20       1832     belgium            Standard Liege   
24      2020  23/08/20       1832     belgium               Club Brugge   
25      2020  23/08/20       1832     belgium                Anderlecht   
26      2020  24/08/20       1832     belgium             St. Truidense   
27      2020  28/08/20       1832     belgium               KV Oostende   
28      2020  29/08/20       1832     belgium                     Eupen   
29      2020  29/08/20       1832     belgium          Waasland-Beveren   
30      2020  29/08/20       1832     belgium             Cercle Brugge   
31      2020  29/08/20       1832     belgium         Mouscron-Peruwelz   
32      2020  30/08/20       1832     belgium                      Genk   
33      2020  30/08/20       1832     belgium    KFCO Beerschot-Wilrijk   
34      2020  30/08/20       1832     belgium     Sporting de Charleroi   
35      2020  30/08/20       1832     belgium                  KAA Gent   
36      2020  11/09/20       1832     belgium                     Eupen   
37      2020  12/09/20       1832     belgium               KV Mechelen   
38      2020  12/09/20       1832     belgium                 OH Leuven   
39      2020  12/09/20       1832     belgium               Club Brugge   
40      2020  13/09/20       1832     belgium                Anderlecht   
41      2020  13/09/20       1832     belgium             St. Truidense   
42      2020  13/09/20       1832     belgium          SV Zulte Waregem   
43      2020  13/09/20       1832     belgium               KV Kortrijk   
44      2020  14/09/20       1832     belgium    KFCO Beerschot-Wilrijk   
45      2020  18/09/20       1832     belgium     Sporting de Charleroi   
46      2020  19/09/20       1832     belgium               KV Oostende   
47      2020  19/09/20       1832     belgium         Mouscron-Peruwelz   
48      2020  19/09/20       1832     belgium          Waasland-Beveren   
49      2020  20/09/20       1832     belgium          SV Zulte Waregem   
50      2020  20/09/20       1832     belgium            Standard Liege   
51      2020  20/09/20       1832     belgium                      Genk   
52      2020  20/09/20       18

## Aligning team names from two different data set

In [9]:
'''team_names_uk= []
for direction in os.listdir("football_data_uk"):
    
    league = pd.read_csv("football_data_uk/{}".format(direction))
    team_names_uk.extend(list(league["HomeTeam"].unique()))'''

'team_names_uk= []\nfor direction in os.listdir("football_data_uk"):\n    \n    league = pd.read_csv("football_data_uk/{}".format(direction))\n    team_names_uk.extend(list(league["HomeTeam"].unique()))'

In [10]:
#Team names from data set from fivethirtyeight.com
'''team_names_five = list(leagues_datas["HomeTeam"].unique())
team_names_dict = {}

for team_five in team_names_five:
    for team_uk in team_names_uk:
        if team_five == team_uk: 
            #adding match team names in the dictionary
            team_names_dict[team_five] = team_uk
            #removing matching teams for detecting non_mathces
            team_names_uk.remove(team_uk)
            team_names_five.remove(team_five)'''
  

'team_names_five = list(leagues_datas["HomeTeam"].unique())\nteam_names_dict = {}\n\nfor team_five in team_names_five:\n    for team_uk in team_names_uk:\n        if team_five == team_uk: \n            #adding match team names in the dictionary\n            team_names_dict[team_five] = team_uk\n            #removing matching teams for detecting non_mathces\n            team_names_uk.remove(team_uk)\n            team_names_five.remove(team_five)'

In [11]:
'''for i in team_names_uk:
    print(i)'''

'for i in team_names_uk:\n    print(i)'

In [12]:
'''for i in team_names_five:
    
    x = input(" {} : ".format(i)  )
    
    team_names_dict[i] = x
'''    

'for i in team_names_five:\n    \n    x = input(" {} : ".format(i)  )\n    \n    team_names_dict[i] = x\n'

In [13]:
#filehandler = open("team_dicts", "wb")
#dump(team_names_dict,filehandler)

In [14]:
#loading pickled dictonary of team names 
filehandler = open("team_dicts", "rb")
team_names_dict = load(filehandler)
team_names_dict

{'Club Brugge': 'Club Brugge',
 'Antwerp': 'Antwerp',
 'Genk': 'Genk',
 'Cercle Brugge': 'Cercle Brugge',
 'Eupen': 'Eupen',
 'Waasland-Beveren': 'Waasland-Beveren',
 'Lille': 'Lille',
 'Nimes': 'Nimes',
 'Nice': 'Nice',
 'Strasbourg': 'Strasbourg',
 'Nantes': 'Nantes',
 'Metz': 'Metz',
 'Brest': 'Brest',
 'Montpellier': 'Montpellier',
 'Marseille': 'Marseille',
 'Sivasspor': 'Sivasspor',
 'Galatasaray': 'Galatasaray',
 'Kayserispor': 'Kayserispor',
 'Trabzonspor': 'Trabzonspor',
 'Yeni Malatyaspor': 'Yeni Malatyaspor',
 'Denizlispor': 'Denizlispor',
 'Alanyaspor': 'Alanyaspor',
 'Kasimpasa': 'Kasimpasa',
 'Fenerbahce': 'Fenerbahce',
 'Fulham': 'Fulham',
 'Liverpool': 'Liverpool',
 'Sheffield United': 'Sheffield United',
 'Everton': 'Everton',
 'Arsenal': 'Arsenal',
 'Newcastle': 'Newcastle',
 'Aston Villa': 'Aston Villa',
 'Burnley': 'Burnley',
 'Eibar': 'Eibar',
 'Cadiz': 'Cadiz',
 'Villarreal': 'Villarreal',
 'Getafe': 'Getafe',
 'Elche': 'Elche',
 'Barcelona': 'Barcelona',
 'Levant

In [15]:
#Changing varied team names into one for a team
leagues_datas["HomeTeam"] = leagues_datas["HomeTeam"].map( team_names_dict)
leagues_datas["AwayTeam"] = leagues_datas["AwayTeam"].map(team_names_dict)

try:
    os.mkdir("league_datas")
except:
    "File Already Exists"
    pass
leagues = list(leagues_datas["league"].unique())
for league in leagues:
    data_index = leagues_datas["league"][lambda x: x == league].index
    data_frame = leagues_datas.loc[data_index]
    csv_dir= "{}".format(league)
    data_frame.to_csv("league_datas/{}.csv".format( csv_dir),index=False)

## Combining Two Data Sets Together

In [16]:
def column_placer(data_set,updated_data,league ) :
    
    away_home = {"away" : "AwayTeam", "home" : "HomeTeam"}
    
    #Features will be seperated according dictionaries below
    away_features = { "AW" : "W", "AD" : "D", "AL" : "L", "FTAG" : "FTG", "HTAG" : "HTG", "FTAGC" : "FTGC", "HTAGC" : "HTGC",
                     "AS" : "S", "AST" : "ST", "AF": "F", "AC" : "C", "AY" : "Y", "AR" : "R"}
    home_features = { "HW" : "W", "HD" : "D", "HL" : "L", "FTHG" : "FTG", "FTHGC" : "FTGC", "HTHGC" : "HTGC",
                     "HTHG" : "HTG", "HS" : "S", "HST" : "ST", "HF": "F", "HC" : "C", "HY" : "Y", "HR" : "R"}
    
    
    #Condition according to choice of "data_set" argument  
    
    if away_home[data_set] == "AwayTeam":
        
        data_features = away_features
    else:
        
        data_features = home_features
    
    #Itreation of each data feature
    for feature in data_features:
        
        column_scalars= []
        
        for i in range(updated_data.shape[0]):
            
            team = updated_data[ away_home[data_set] ][i]
            date = updated_data["date"][i]
            
            #Loading indiviual team datas
            data = pd.read_csv("team_league_data/{}/{}.csv".format(league, team ))
            
            #Reshaping "date" column scalars accoring to updated data set. 
            if len(data["Date"][0])>8:
                data["Date"] = data.apply(lambda row: row["Date"][0:6] + row["Date"][-2:], axis=1)
            
            #Error handing for nan valued scalar in a team's data set
            try: 
                match_index = data["Date"][data["Date"] == date].index[0]
                column_scalars.append(data[data_features[feature]].loc[match_index])
            except IndexError:
                print("An Error Occured : ", date, team)
                column_scalars.append(None)
        
        #Adding new features with its scalars
        updated_data[feature] = column_scalars
    
    updated_data.to_csv("data_sets/{}.csv".format(league),index = False)

## Creating Belgium Training Data Set

In [17]:
#Data generated from fivethirtytwo data set
belgium_five = pd.read_csv("league_datas/belgium.csv")

In [18]:
belgium_five.shape

(306, 17)

In [19]:
belgium_uk = pd.read_csv("football_data_uk/belgium.csv")

In [20]:
belgium_five

season      date  league_id   league             HomeTeam  \
0      2020  08/08/20       1832  belgium          Club Brugge   
1      2020  08/08/20       1832  belgium             Standard   
2      2020  08/08/20       1832  belgium              Antwerp   
3      2020  09/08/20       1832  belgium           St Truiden   
4      2020  09/08/20       1832  belgium              Waregem   
5      2020  09/08/20       1832  belgium             Mechelen   
6      2020  09/08/20       1832  belgium             Kortrijk   
7      2020  10/08/20       1832  belgium  Oud-Heverlee Leuven   
8      2020  10/08/20       1832  belgium             Oostende   
9      2020  14/08/20       1832  belgium             Mouscron   
10     2020  15/08/20       1832  belgium                 Genk   
11     2020  15/08/20       1832  belgium                 Gent   
12     2020  15/08/20       1832  belgium            Charleroi   
13     2020  16/08/20       1832  belgium        Cercle Brugge   
14     2020  16/08/20       1832  belgium         Beerschot VA   
15     2020  16/08/20       1832  belgium                Eupen   
16     2020  16/08/20       1832  belgium           Anderlecht   
17     2020  17/08/20       1832  belgium     Waasland-Beveren   
18     2020  21/08/20       1832  belgium             Kortrijk   
19     2020  22/08/20       1832  belgium              Waregem   
20     2020  22/08/20       1832  belgium             Mechelen   
21     2020  22/08/20       1832  belgium  Oud-Heverlee Leuven   
22     2020  22/08/20       1832  belgium              Antwerp   
23     2020  23/08/20       1832  belgium             Standard   
24     2020  23/08/20       1832  belgium          Club Brugge   
25     2020  23/08/20       1832  belgium           Anderlecht   
26     2020  24/08/20       1832  belgium           St Truiden   
27     2020  28/08/20       1832  belgium             Oostende   
28     2020  29/08/20       1832  belgium                Eupen   
29     2020  29/08/20       1832  belgium     Waasland-Beveren   
30     2020  29/08/20       1832  belgium        Cercle Brugge   
31     2020  29/08/20       1832  belgium             Mouscron   
32     2020  30/08/20       1832  belgium                 Genk   
33     2020  30/08/20       1832  belgium         Beerschot VA   
34     2020  30/08/20       1832  belgium            Charleroi   
35     2020  30/08/20       1832  belgium                 Gent   
36     2020  11/09/20       1832  belgium                Eupen   
37     2020  12/09/20       1832  belgium             Mechelen   
38     2020  12/09/20       1832  belgium  Oud-Heverlee Leuven   
39     2020  12/09/20       1832  belgium          Club Brugge   
40     2020  13/09/20       1832  belgium           Anderlecht   
41     2020  13/09/20       1832  belgium           St Truiden   
42     2020  13/09/20       1832  belgium              Waregem   
43     2020  13/09/20       1832  belgium             Kortrijk   
44     2020  14/09/20       1832  belgium         Beerschot VA   
45     2020  18/09/20       1832  belgium            Charleroi   
46     2020  19/09/20       1832  belgium             Oostende   
47     2020  19/09/20       1832  belgium             Mouscron   
48     2020  19/09/20       1832  belgium     Waasland-Beveren   
49     2020  20/09/20       1832  belgium              Waregem   
50     2020  20/09/20       1832  belgium             Standard   
51     2020  20/09/20       1832  belgium                 Genk   
52     2020  20/09/20       1832  belgium              Antwerp   
53     2020  21/09/20       1832  belgium        Cercle Brugge   
54     2020  25/09/20       1832  belgium             Kortrijk   
55     2020  26/09/20       1832  belgium         Beerschot VA   
56     2020  26/09/20       1832  belgium             Mechelen   
57     2020  26/09/20       1832  belgium                 Gent   
58     2020  27/09/20       1832  belgium             Standard   
59     2020  27/09/20       1832  belgium    

In [21]:
belgium_uk

Div        Date   Time             HomeTeam             AwayTeam  FTHG  \
0    B1  08/08/2020  15:30          Club Brugge            Charleroi     0   
1    B1  08/08/2020  18:00              Antwerp             Mouscron     1   
2    B1  08/08/2020  18:00             Standard        Cercle Brugge     1   
3    B1  09/08/2020  12:30           St Truiden                 Gent     2   
4    B1  09/08/2020  15:00              Waregem                 Genk     1   
5    B1  09/08/2020  17:15             Mechelen           Anderlecht     2   
6    B1  09/08/2020  19:45             Kortrijk     Waasland-Beveren     1   
7    B1  10/08/2020  18:00  Oud-Heverlee Leuven                Eupen     1   
8    B1  10/08/2020  18:00             Oostende         Beerschot VA     1   
9    B1  14/08/2020  18:00             Mouscron             Mechelen     0   
10   B1  15/08/2020  15:30                 Genk  Oud-Heverlee Leuven     1   
11   B1  15/08/2020  18:00            Charleroi             Oostende     1   
12   B1  15/08/2020  18:00                 Gent             Kortrijk     1   
13   B1  16/08/2020  12:30        Cercle Brugge              Antwerp     2   
14   B1  16/08/2020  15:00         Beerschot VA              Waregem     3   
15   B1  16/08/2020  15:00                Eupen          Club Brugge     0   
16   B1  16/08/2020  17:15           Anderlecht           St Truiden     3   
17   B1  17/08/2020  18:00     Waasland-Beveren             Standard     1   
18   B1  21/08/2020  18:00             Kortrijk                Eupen     0   
19   B1  22/08/2020  15:15              Waregem     Waasland-Beveren     4   
20   B1  22/08/2020  17:30             Mechelen        Cercle Brugge     2   
21   B1  22/08/2020  17:30  Oud-Heverlee Leuven            Charleroi     1   
22   B1  22/08/2020  19:45              Antwerp                 Gent     1   
23   B1  23/08/2020  12:30             Standard                 Genk     0   
24   B1  23/08/2020  15:00          Club Brugge         Beerschot VA     0   
25   B1  23/08/2020  17:15           Anderlecht             Mouscron     1   
26   B1  24/08/2020  19:45           St Truiden             Oostende     0   
27   B1  28/08/2020  19:45             Oostende           Anderlecht     2   
28   B1  29/08/2020  15:15                Eupen           St Truiden     1   
29   B1  29/08/2020  17:30        Cercle Brugge             Kortrijk     0   
30   B1  29/08/2020  17:30     Waasland-Beveren  Oud-Heverlee Leuven     1   
31   B1  29/08/2020  19:45             Mouscron              Waregem     0   
32   B1  30/08/2020  12:30                 Genk          Club Brugge     1   
33   B1  30/08/2020  15:00         Beerschot VA             Standard     0   
34   B1  30/08/2020  17:15            Charleroi              Antwerp     2   
35   B1  30/08/2020  19:45                 Gent             Mechelen     1   
36   B1  11/09/2020  19:45                Eupen                 Gent     2   
37   B1  12/09/2020  15:15             Mechelen             Oostende     0   
38   B1  12/09/2020  17:30  Oud-Heverlee Leuven             Standard     1   
39   B1  12/09/2020  19:45          Club Brugge     Waasland-Beveren     4   
40   B1  13/09/2020  12:30           Anderlecht        Cercle Brugge     2   
41   B1  13/09/2020  15:00           St Truiden              Antwerp     2   
42   B1  13/09/2020  17:15              Waregem            Charleroi     0   
43   B1  13/09/2020  19:45             Kortrijk             Mouscron     3   
44   B1  14/09/2020  19:45         Beerschot VA                 Genk     5   
45   B1  18/09/2020  19:45            Charleroi         Beerschot VA     3   
46   B1  19/09/2020  15:15             Oostende  Oud-Heverlee Leuven     3   
47   B1  19/09/2020  17:30             Mouscron                 Gent     0   
48   B1  19/09/2020  19:45     Waasland-Beveren           Anderlecht     2   
49   B1  20/09/2020  12:30              Waregem          Club Brugge     0   
50   B1  20/09/2020  15:00

In [22]:
#Indices until first "nan" score
data_updated = belgium_five.loc[:257]
data_updated

season      date  league_id   league             HomeTeam  \
0      2020  08/08/20       1832  belgium          Club Brugge   
1      2020  08/08/20       1832  belgium             Standard   
2      2020  08/08/20       1832  belgium              Antwerp   
3      2020  09/08/20       1832  belgium           St Truiden   
4      2020  09/08/20       1832  belgium              Waregem   
5      2020  09/08/20       1832  belgium             Mechelen   
6      2020  09/08/20       1832  belgium             Kortrijk   
7      2020  10/08/20       1832  belgium  Oud-Heverlee Leuven   
8      2020  10/08/20       1832  belgium             Oostende   
9      2020  14/08/20       1832  belgium             Mouscron   
10     2020  15/08/20       1832  belgium                 Genk   
11     2020  15/08/20       1832  belgium                 Gent   
12     2020  15/08/20       1832  belgium            Charleroi   
13     2020  16/08/20       1832  belgium        Cercle Brugge   
14     2020  16/08/20       1832  belgium         Beerschot VA   
15     2020  16/08/20       1832  belgium                Eupen   
16     2020  16/08/20       1832  belgium           Anderlecht   
17     2020  17/08/20       1832  belgium     Waasland-Beveren   
18     2020  21/08/20       1832  belgium             Kortrijk   
19     2020  22/08/20       1832  belgium              Waregem   
20     2020  22/08/20       1832  belgium             Mechelen   
21     2020  22/08/20       1832  belgium  Oud-Heverlee Leuven   
22     2020  22/08/20       1832  belgium              Antwerp   
23     2020  23/08/20       1832  belgium             Standard   
24     2020  23/08/20       1832  belgium          Club Brugge   
25     2020  23/08/20       1832  belgium           Anderlecht   
26     2020  24/08/20       1832  belgium           St Truiden   
27     2020  28/08/20       1832  belgium             Oostende   
28     2020  29/08/20       1832  belgium                Eupen   
29     2020  29/08/20       1832  belgium     Waasland-Beveren   
30     2020  29/08/20       1832  belgium        Cercle Brugge   
31     2020  29/08/20       1832  belgium             Mouscron   
32     2020  30/08/20       1832  belgium                 Genk   
33     2020  30/08/20       1832  belgium         Beerschot VA   
34     2020  30/08/20       1832  belgium            Charleroi   
35     2020  30/08/20       1832  belgium                 Gent   
36     2020  11/09/20       1832  belgium                Eupen   
37     2020  12/09/20       1832  belgium             Mechelen   
38     2020  12/09/20       1832  belgium  Oud-Heverlee Leuven   
39     2020  12/09/20       1832  belgium          Club Brugge   
40     2020  13/09/20       1832  belgium           Anderlecht   
41     2020  13/09/20       1832  belgium           St Truiden   
42     2020  13/09/20       1832  belgium              Waregem   
43     2020  13/09/20       1832  belgium             Kortrijk   
44     2020  14/09/20       1832  belgium         Beerschot VA   
45     2020  18/09/20       1832  belgium            Charleroi   
46     2020  19/09/20       1832  belgium             Oostende   
47     2020  19/09/20       1832  belgium             Mouscron   
48     2020  19/09/20       1832  belgium     Waasland-Beveren   
49     2020  20/09/20       1832  belgium              Waregem   
50     2020  20/09/20       1832  belgium             Standard   
51     2020  20/09/20       1832  belgium                 Genk   
52     2020  20/09/20       1832  belgium              Antwerp   
53     2020  21/09/20       1832  belgium        Cercle Brugge   
54     2020  25/09/20       1832  belgium             Kortrijk   
55     2020  26/09/20       1832  belgium         Beerschot VA   
56     2020  26/09/20       1832  belgium             Mechelen   
57     2020  26/09/20       1832  belgium                 Gent   
58     2020  27/09/20       1832  belgium             Standard   
59     2020  27/09/20       1832  belgium    

In [23]:
column_placer("home", data_updated, "belgium")
column_placer("away", data_updated, "belgium")

An Error Occured :  14/02/21 Charleroi


C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Charleroi
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge
An Error Occured :  14/02/21 Club Brugge

## Creating England Training Data Set

In [24]:
england_five = pd.read_csv("league_datas/england.csv")
#england_five

In [25]:
england_uk = pd.read_csv("football_data_uk/england.csv")
#england_uk

In [26]:
data_updated = england_five.loc[:262]


In [27]:
column_placer("home", data_updated, "england")
column_placer("away", data_updated, "england")

An Error Occured :  17/01/21 Aston Villa


C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Aston Villa
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton
An Error Occured :  17/01/21 Everton


## Creating France Training Data Set

In [28]:
france_five = pd.read_csv("league_datas/france.csv")
france_uk = pd.read_csv("football_data_uk/france.csv")

In [29]:
france_five

season      date  league_id  league     HomeTeam     AwayTeam   spi1  \
0      2020  21/08/20       1843  france     Bordeaux       Nantes  59.92   
1      2020  22/08/20       1843  france        Dijon       Angers  54.91   
2      2020  22/08/20       1843  france        Lille       Rennes  70.39   
3      2020  23/08/20       1843  france       Monaco        Reims  67.42   
4      2020  23/08/20       1843  france        Nimes        Brest  54.60   
5      2020  23/08/20       1843  france      Lorient   Strasbourg  52.87   
6      2020  23/08/20       1843  france         Nice         Lens  59.29   
7      2020  28/08/20       1843  france         Lyon        Dijon  73.68   
8      2020  29/08/20       1843  france       Rennes  Montpellier  66.79   
9      2020  29/08/20       1843  france   Strasbourg         Nice  58.50   
10     2020  30/08/20       1843  france        Reims        Lille  58.30   
11     2020  30/08/20       1843  france       Nantes        Nimes  59.93   
12     2020  30/08/20       1843  france       Angers     Bordeaux  60.95   
13     2020  30/08/20       1843  france         Metz       Monaco  53.27   
14     2020  30/08/20       1843  france   St Etienne      Lorient  56.09   
15     2020  30/08/20       1843  france        Brest    Marseille  53.20   
16     2020  10/09/20       1843  france         Lens     Paris SG  55.46   
17     2020  11/09/20       1843  france     Bordeaux         Lyon  61.68   
18     2020  12/09/20       1843  france  Montpellier         Nice  59.80   
19     2020  12/09/20       1843  france   St Etienne   Strasbourg  57.15   
20     2020  13/09/20       1843  france        Lille         Metz  69.97   
21     2020  13/09/20       1843  france        Dijon        Brest  51.64   
22     2020  13/09/20       1843  france      Lorient         Lens  53.87   
23     2020  13/09/20       1843  france       Angers        Reims  58.91   
24     2020  13/09/20       1843  france        Nimes       Rennes  56.33   
25     2020  13/09/20       1843  france       Monaco       Nantes  67.13   
26     2020  13/09/20       1843  france     Paris SG    Marseille  89.65   
27     2020  15/09/20       1843  france  Montpellier         Lyon  61.17   
28     2020  16/09/20       1843  france     Paris SG         Metz  89.11   
29     2020  17/09/20       1843  france    Marseille   St Etienne  66.58   
30     2020  18/09/20       1843  france         Lyon        Nimes  75.82   
31     2020  19/09/20       1843  france         Lens     Bordeaux  58.87   
32     2020  19/09/20       1843  france       Rennes       Monaco  67.33   
33     2020  20/09/20       1843  france         Nice     Paris SG  57.50   
34     2020  20/09/20       1843  france        Brest      Lorient  56.16   
35     2020  20/09/20       1843  france   Strasbourg        Dijon  56.73   
36     2020  20/09/20       1843  france         Metz        Reims  54.90   
37     2020  20/09/20       1843  france  Montpellier       Angers  61.44   
38     2020  20/09/20       1843  france       Nantes   St Etienne  59.14   
39     2020  20/09/20       1843  france    Marseille        Lille  66.09   
40     2020  25/09/20       1843  france        Lille       Nantes  70.51   
41     2020  26/09/20       1843  france   St Etienne       Rennes  57.52   
42     2020  26/09/20       1843  france    Marseille         Metz  65.40   
43     2020  27/09/20       1843  france     Bordeaux         Nice  59.17   
44     2020  27/09/20       1843  france       Monaco   Strasbourg  67.40   
45     2020  27/09/20       1843  france       Angers        Brest  58.84   
46     2020  27/09/20       1843  france        Dijon  Montpellier  48.56   
47     2020  27/09/20       1843  france        Nimes         Lens  55.80   
48     2020  27/09/20       1843  france      Lorient         Lyon  52.12   
49     2020  27/09/20       1843  france        Reims     Paris SG  55.78   
50     2020  02/10/20       1843  france     Paris SG       Angers  89.80   
5

In [30]:
#france_uk

In [31]:
data_updated = france_five.loc[:278]

In [32]:
column_placer("home", data_updated, "france")
column_placer("away", data_updated, "france")

C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


## Creating Germany Training Data Set

In [33]:
germany_five = pd.read_csv("league_datas/germany.csv")
data_updated = germany_five.loc[:205]

In [34]:
column_placer("home", data_updated, "germany")
column_placer("away", data_updated, "germany")

C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


## Creating Italy Training Data Set

In [35]:
italy_five = pd.read_csv("league_datas/italy.csv")
data_updated = italy_five.loc[:246]

In [36]:
column_placer("home", data_updated, "italy")
column_placer("away", data_updated, "italy")

An Error Occured :  02/03/21 Lazio


C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Lazio
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino
An Error Occured :  02/03/21 Torino


## Creating Netherland Training Data Set

In [37]:
netherland_five = pd.read_csv("league_datas/netherland.csv")
#netherland_five

In [38]:
data_updated = netherland_five.loc[:214]
column_placer("home", data_updated, "netherland")
column_placer("away", data_updated, "netherland")

An Error Occured :  07/02/21 Ajax


C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Ajax
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht
An Error Occured :  07/02/21 Utrecht


## Creating Portugal Training Data Set

In [39]:
portugal_five = pd.read_csv("league_datas/portugal.csv")
#portugal_five

In [40]:
data_updated = portugal_five.loc[:188]
column_placer("home", data_updated, "portugal")
column_placer("away", data_updated, "portugal")

C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


## Creating Spain Training Data Set

In [41]:
spain_five = pd.read_csv("league_datas/spain.csv")
#spain_five

In [42]:
data_updated = spain_five.loc[:247]
column_placer("home", data_updated, "spain")
column_placer("away", data_updated, "spain")

C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


## Creating Turkey Training Data Set

In [43]:
turkey_five = pd.read_csv("league_datas/turkey.csv")
turkey_five

season      date  league_id  league          HomeTeam          AwayTeam  \
0      2020  11/09/20       1882  turkey          Rizespor        Fenerbahce   
1      2020  12/09/20       1882  turkey         Sivasspor        Alanyaspor   
2      2020  12/09/20       1882  turkey        Karagumruk  Yeni Malatyaspor   
3      2020  12/09/20       1882  turkey            Goztep       Denizlispor   
4      2020  12/09/20       1882  turkey       Galatasaray         Gaziantep   
5      2020  13/09/20       1882  turkey        Ankaragucu        Erzurum BB   
6      2020  13/09/20       1882  turkey       Kayserispor         Kasimpasa   
7      2020  13/09/20       1882  turkey       Antalyaspor    Genclerbirligi   
8      2020  13/09/20       1882  turkey       Trabzonspor          Besiktas   
9      2020  14/09/20       1882  turkey         Hatayspor        Buyuksehyr   
10     2020  18/09/20       1882  turkey  Yeni Malatyaspor            Goztep   
11     2020  19/09/20       1882  turkey    Genclerbirligi         Konyaspor   
12     2020  19/09/20       1882  turkey       Denizlispor       Trabzonspor   
13     2020  19/09/20       1882  turkey          Besiktas       Antalyaspor   
14     2020  19/09/20       1882  turkey        Alanyaspor       Kayserispor   
15     2020  20/09/20       1882  turkey        Erzurum BB         Sivasspor   
16     2020  20/09/20       1882  turkey         Kasimpasa          Rizespor   
17     2020  20/09/20       1882  turkey         Gaziantep        Karagumruk   
18     2020  20/09/20       1882  turkey        Buyuksehyr       Galatasaray   
19     2020  21/09/20       1882  turkey        Fenerbahce         Hatayspor   
20     2020  25/09/20       1882  turkey        Karagumruk        Buyuksehyr   
21     2020  26/09/20       1882  turkey       Kayserispor        Erzurum BB   
22     2020  26/09/20       1882  turkey            Goztep         Gaziantep   
23     2020  26/09/20       1882  turkey         Hatayspor         Kasimpasa   
24     2020  26/09/20       1882  turkey       Trabzonspor  Yeni Malatyaspor   
25     2020  27/09/20       1882  turkey          Rizespor        Alanyaspor   
26     2020  27/09/20       1882  turkey         Konyaspor          Besiktas   
27     2020  27/09/20       1882  turkey         Sivasspor        Ankaragucu   
28     2020  27/09/20       1882  turkey       Galatasaray        Fenerbahce   
29     2020  28/09/20       1882  turkey       Antalyaspor       Denizlispor   
30     2020  02/10/20       1882  turkey         Gaziantep       Trabzonspor   
31     2020  02/10/20       1882  turkey        Ankaragucu       Kayserispor   
32     2020  03/10/20       1882  turkey  Yeni Malatyaspor       Antalyaspor   
33     2020  03/10/20       1882  turkey        Buyuksehyr            Goztep   
34     2020  03/10/20       1882  turkey        Erzurum BB          Rizespor   
35     2020  03/10/20       1882  turkey        Fenerbahce        Karagumruk   
36     2020  04/10/20       1882  turkey       Denizlispor         Konyaspor   
37     2020  04/10/20       1882  turkey        Alanyaspor         Hatayspor   
38     2020  04/10/20       1882  turkey          Besiktas    Genclerbirligi   
39     2020  04/10/20       1882  turkey         Kasimpasa       Galatasaray   
40     2020  17/10/20       1882  turkey          Rizespor        Ankaragucu   
41     2020  17/10/20       1882  turkey         Konyaspor  Yeni Malatyaspor   
42     2020  17/10/20       1882  turkey       Kayserispor         Sivasspor   
43     2020  17/10/20       1882  turkey       Trabzonspor        Buyuksehyr   
44     2020  18/10/20       1882  turkey       Antalyaspor         Gaziantep   
45     2020  18/10/20       1882  turkey        Karagumruk         Kasimpasa   
46     2020  18/10/20       1882  turkey            Goztep        Fenerbahce   
47     2020  19/10/20       1882  turkey       Galatasaray        Alanyaspor   
48     2020  19/10/20       1882  turkey    Genclerbirligi       Denizlispor   
49   

In [44]:
data_updated = turkey_five.loc[:276]
column_placer("home", data_updated, "turkey")
column_placer("away", data_updated, "turkey")

An Error Occured :  30/01/21 Alanyaspor


C:\Users\HP\Anaconda3\lib\site-packages\ipykernel_launcher.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Alanyaspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
An Error Occured :  30/01/21 Sivasspor
